In [1]:
%pip install torch==2.5.1 torchvision==0.20.1 torchaudio==2.5.1 --index-url https://download.pytorch.org/whl/cu124 --force-reinstall

Looking in indexes: https://download.pytorch.org/whl/cu124
     ---------------------------------------- 0.0/2.5 GB ? eta -:--:--
     ---------------------------------------- 0.0/2.5 GB ? eta -:--:--
     ---------------------------------------- 0.0/2.5 GB ? eta -:--:--
     ---------------------------------------- 0.0/2.5 GB 796.8 kB/s eta 0:52:31
     ---------------------------------------- 0.0/2.5 GB 796.8 kB/s eta 0:52:31
     ---------------------------------------- 0.0/2.5 GB 744.7 kB/s eta 0:56:11
     ---------------------------------------- 0.0/2.5 GB 824.4 kB/s eta 0:50:45
     ---------------------------------------- 0.0/2.5 GB 849.0 kB/s eta 0:49:16
     ---------------------------------------- 0.0/2.5 GB 855.6 kB/s eta 0:48:53
     ---------------------------------------- 0.0/2.5 GB 898.8 kB/s eta 0:46:32
     ---------------------------------------- 0.0/2.5 GB 898.8 kB/s eta 0:46:32
     ---------------------------------------- 0.0/2.5 GB 924.4 kB/s eta 0:45:14
     ---

In [2]:
import torch

def format_pytorch_version(version_str):
    # Example input: "2.0.1+cu118" -> returns "2.0.1"
    return version_str.split('+')[0]

def format_cuda_version(cuda_str):
    # If CUDA is None (CPU-only PyTorch), return "cpu"
    if cuda_str is None:
        return "cpu"
    # Example: "11.8" -> "cu118"
    return "cu" + cuda_str.replace('.', '')

TORCH_version = torch.__version__
TORCH = format_pytorch_version(TORCH_version)
CUDA_version = torch.version.cuda
CUDA = format_cuda_version(CUDA_version)

print(f"Installing packages for torch-{TORCH}+{CUDA}...")

%pip install --upgrade --no-cache-dir pyg_lib torch_scatter torch_sparse torch_cluster torch_spline_conv -f https://data.pyg.org/whl/torch-{TORCH}+{CUDA}.html

%pip install torch_geometric

Installing packages for torch-2.5.1+cu124...
Looking in links: https://data.pyg.org/whl/torch-2.5.1+cu124.html
     ---------------------------------------- 0.0/1.7 MB ? eta -:--:--
     ------ --------------------------------- 0.3/1.7 MB ? eta -:--:--
     ------------ --------------------------- 0.5/1.7 MB 2.1 MB/s eta 0:00:01
     ------------------ --------------------- 0.8/1.7 MB 1.1 MB/s eta 0:00:01
     ------------------------ --------------- 1.0/1.7 MB 1.3 MB/s eta 0:00:01
     ---------------------------------------- 1.7/1.7 MB 1.7 MB/s eta 0:00:00
     ---------------------------------------- 0.0/3.5 MB ? eta -:--:--
     ------ --------------------------------- 0.5/3.5 MB 2.8 MB/s eta 0:00:02
     ------------ --------------------------- 1.0/3.5 MB 2.5 MB/s eta 0:00:01
     ------------------ --------------------- 1.6/3.5 MB 2.5 MB/s eta 0:00:01
     --------------------- ------------------ 1.8/3.5 MB 2.6 MB/s eta 0:00:01
     --------------------------- ------------ 2.4/3.

In [4]:
%pip install scikit-learn imbalanced-learn xgboost

  Using cached joblib-1.4.2-py3-none-any.whl.metadata (5.4 kB)
  Using cached threadpoolctl-3.5.0-py3-none-any.whl.metadata (13 kB)
   ---------------------------------------- 0.0/11.1 MB ? eta -:--:--
   - -------------------------------------- 0.5/11.1 MB 2.8 MB/s eta 0:00:04
   --- ------------------------------------ 1.0/11.1 MB 2.7 MB/s eta 0:00:04
   ---- ----------------------------------- 1.3/11.1 MB 2.7 MB/s eta 0:00:04
   ---- ----------------------------------- 1.3/11.1 MB 2.7 MB/s eta 0:00:04
   ---- ----------------------------------- 1.3/11.1 MB 2.7 MB/s eta 0:00:04
   ----- ---------------------------------- 1.6/11.1 MB 1.2 MB/s eta 0:00:08
   ------ --------------------------------- 1.8/11.1 MB 1.2 MB/s eta 0:00:08
   ------ --------------------------------- 1.8/11.1 MB 1.2 MB/s eta 0:00:08
   ------- -------------------------------- 2.1/11.1 MB 1.1 MB/s eta 0:00:09
   ------- -------------------------------- 2.1/11.1 MB 1.1 MB/s eta 0:00:09
   -------- ----------------

In [6]:
%pip install optuna

   ---------------------------------------- 0.0/2.1 MB ? eta -:--:--
   ---------------------------------------- 0.0/2.1 MB ? eta -:--:--
   ---- ----------------------------------- 0.3/2.1 MB ? eta -:--:--
   -------------- ------------------------- 0.8/2.1 MB 1.3 MB/s eta 0:00:02
   ------------------- -------------------- 1.0/2.1 MB 1.3 MB/s eta 0:00:01
   ----------------------------- ---------- 1.6/2.1 MB 1.6 MB/s eta 0:00:01
   ---------------------------------- ----- 1.8/2.1 MB 1.7 MB/s eta 0:00:01
   ---------------------------------------- 2.1/2.1 MB 1.7 MB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.


### Hyperparameter Optimization Citeseer
#### SCAR 

In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "citeseer",      
        "mechanism": "SCAR",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 13, 27),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64,128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64,128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0, 0.5),
        "margin": 0.5,
        "lpl_weight": 0.5,#trial.suggest_float("lpl_weight", 0.01, 0.99),
        "ratio": trial.suggest_float("ratio", 0.08, 0.28),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ['sum', 'mean']),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "model_type": trial.suggest_categorical("model_type", ['GCNConv', 'GATConv', 'SAGEConv', 'GINConv', 'TransformerConv']),
        "sampling_mode":trial.suggest_categorical("sampling_mode", [None,'nn', 'random', 'feature']), #'weighted',
        "num_neighbors": trial.suggest_int("num_neighbors", 5, 20),
        "seeds": 5,
        "output_csv": "citeseer_scar_conv_sampling.csv"
    }
    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=200)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "citeseer",      
        "mechanism": "SCAR",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 13, 27),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0, 0.5),
        "margin": 0.5,
        "lpl_weight": 0.5,#trial.suggest_float("lpl_weight", 0.01, 0.99),
        "ratio": trial.suggest_float("ratio", 0.08, 0.28),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ['sum', 'mean']),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "seeds": 5,
        "output_csv": "citeseer_scar_learnable_params_fixed_lambda.csv"
    }
    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=200)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-02-27 14:29:50,880] A new study created in memory with name: no-name-e71d36aa-359b-4e47-a98c-64f2af809de4


Running experiment with seed=1:
 - alpha=0.5, K=14, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.15465785032777538, pos_weight=1, aggregation=sum, treatment=relabeling
Epoch 0, Loss: 0.5433, LPL: 0.9189, Contrastive: 0.1677
Epoch 50, Loss: 0.4595, LPL: 0.9189, Contrastive: 0.0000
Epoch 100, Loss: 6.2865, LPL: 12.5726, Contrastive: 0.0003
 - Metrics: Accuracy=0.8810, F1=0.7381, Recall=0.7960, Precision=0.6880
Running experiment with seed=2:
 - alpha=0.5, K=14, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.15465785032777538, pos_weight=1, aggregation=sum, treatment=relabeling
Epoch 0, Loss: 0.4909, LPL: 0.7754, Contrastive: 0.2063
Epoch 50, Loss: 0.3877, LPL: 0.7754, Contrastive: 0.0000
Epoch 100, Loss: 6.2809, LPL: 12.5615, Contrastive: 0.0004
 - Metrics: Accuracy=0.8810, F1=0.7381, Recall=0.7960, Precision=0.6880
Running experiment with seed=3:
 - alpha=0.5, K=14, layers=2, hidden=256, out=25

[I 2025-02-27 14:31:31,619] Trial 0 finished with value: 0.7378306878306878 and parameters: {'K': 14, 'layers': 2, 'hidden_channels': 256, 'out_channels': 256, 'ratio': 0.15465785032777538, 'aggregation': 'sum', 'treatment': 'relabeling'}. Best is trial 0 with value: 0.7378306878306878.


 - Metrics: Accuracy=0.8804, F1=0.7368, Recall=0.7946, Precision=0.6868
Done. Results written to citeseer_experimentations\citeseer_scar_learnable_params_fixed_lambda_2702142950.csv.
Average F1 over 5 seeds: 0.7378 ± 0.0117
Running experiment with seed=1:
 - alpha=0.5, K=24, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.11464802998081011, pos_weight=1, aggregation=sum, treatment=relabeling
Epoch 0, Loss: 0.7644, LPL: 1.3846, Contrastive: 0.1441
Epoch 50, Loss: 0.6923, LPL: 1.3846, Contrastive: 0.0000
Epoch 100, Loss: 10.7326, LPL: 21.4649, Contrastive: 0.0004
 - Metrics: Accuracy=0.9059, F1=0.7753, Recall=0.7703, Precision=0.7803
Running experiment with seed=2:
 - alpha=0.5, K=24, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.11464802998081011, pos_weight=1, aggregation=sum, treatment=relabeling
Epoch 0, Loss: 0.5533, LPL: 0.8972, Contrastive: 0.2094
Epoch 50, Loss: 0.4486, LPL: 0.8972, Contra

[I 2025-02-27 14:33:21,776] Trial 1 finished with value: 0.7830581478822685 and parameters: {'K': 24, 'layers': 2, 'hidden_channels': 256, 'out_channels': 256, 'ratio': 0.11464802998081011, 'aggregation': 'sum', 'treatment': 'relabeling'}. Best is trial 1 with value: 0.7830581478822685.


...

 - Metrics: Accuracy=0.9249, F1=0.8175, Recall=0.7989, Precision=0.8371
Done. Results written to citeseer_experimentations\citeseer_scar_learnable_params_fixed_lambda_2702162536.csv.
Average F1 over 5 seeds: 0.8226 ± 0.0064
Running experiment with seed=1:
 - alpha=0.5, K=14, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.21203622232804326, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.6233, LPL: 1.2120, Contrastive: 0.0346
 - Metrics: Accuracy=0.9185, F1=0.8055, Recall=0.8003, Precision=0.8107
Running experiment with seed=2:
 - alpha=0.5, K=14, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.21203622232804326, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.5957, LPL: 1.1501, Contrastive: 0.0414
 - Metrics: Accuracy=0.9294, F1=0.8360, Recall=0.8545, Precision=0.8183
Running experiment with seed=3:
 - alpha=0.5, K=14, layers=2, hidden=256, out=256
 - norm=None

[I 2025-02-27 16:28:12,800] Trial 89 finished with value: 0.8296356882368652 and parameters: {'K': 14, 'layers': 2, 'hidden_channels': 256, 'out_channels': 256, 'ratio': 0.21203622232804326, 'aggregation': 'sum', 'treatment': 'removal'}. Best is trial 83 with value: 0.8303201820774918.


 - Metrics: Accuracy=0.9282, F1=0.8309, Recall=0.8374, Precision=0.8244
Done. Results written to citeseer_experimentations\citeseer_scar_learnable_params_fixed_lambda_2702162708.csv.
Average F1 over 5 seeds: 0.8296 ± 0.0124
Running experiment with seed=1:
 - alpha=0.5, K=19, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.21154885535655601, pos_weight=1, aggregation=sum, treatment=relabeling
Epoch 0, Loss: 0.6051, LPL: 1.0124, Contrastive: 0.1978
Epoch 50, Loss: 0.5062, LPL: 1.0124, Contrastive: 0.0000
Epoch 100, Loss: 8.5132, LPL: 17.0260, Contrastive: 0.0004
 - Metrics: Accuracy=0.8392, F1=0.6817, Recall=0.8174, Precision=0.5847
Running experiment with seed=2:
 - alpha=0.5, K=19, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.21154885535655601, pos_weight=1, aggregation=sum, treatment=relabeling
Epoch 0, Loss: 0.5629, LPL: 0.9238, Contrastive: 0.2021
Epoch 50, Loss: 0.4619, LPL: 0.9238, Contras

[I 2025-02-27 16:30:07,732] Trial 90 finished with value: 0.6879238548483047 and parameters: {'K': 19, 'layers': 2, 'hidden_channels': 256, 'out_channels': 256, 'ratio': 0.21154885535655601, 'aggregation': 'sum', 'treatment': 'relabeling'}. Best is trial 83 with value: 0.8303201820774918.


 - Metrics: Accuracy=0.8458, F1=0.6948, Recall=0.8331, Precision=0.5959
Done. Results written to citeseer_experimentations\citeseer_scar_learnable_params_fixed_lambda_2702162812.csv.
Average F1 over 5 seeds: 0.6879 ± 0.0054
Running experiment with seed=1:
 - alpha=0.5, K=14, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.20765359355802573, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.6227, LPL: 1.2104, Contrastive: 0.0350
 - Metrics: Accuracy=0.9170, F1=0.8040, Recall=0.8074, Precision=0.8006
Running experiment with seed=2:
 - alpha=0.5, K=14, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5
 - ratio=0.20765359355802573, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.5954, LPL: 1.1493, Contrastive: 0.0416


In [4]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "citeseer",      
        "mechanism": "SCAR",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 15, 25),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0, 0.5),
        "margin": 0.5,
        "lpl_weight": trial.suggest_float("lpl_weight", 0.01, 0.99),
        "ratio": trial.suggest_float("ratio", 0.05, 0.25),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ['sum', 'mean']),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "seeds": 5,
        "output_csv": "citeseer_scar_learnable_params.csv"
    }
    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=200)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-02-27 03:17:37,099] A new study created in memory with name: no-name-235d293e-b58f-4219-874c-4d31fec22be7


Running experiment with seed=1:
 - alpha=0.5, K=22, layers=2, hidden=256, out=128
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.19582571123827155
 - ratio=0.0944447007633662, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.3068, LPL: 1.4202, Contrastive: 0.0357
Epoch 50, Loss: 0.2782, LPL: 1.4202, Contrastive: 0.0001
Epoch 100, Loss: 3.8837, LPL: 19.8319, Contrastive: 0.0002
 - Metrics: Accuracy=0.9128, F1=0.7698, Recall=0.6919, Precision=0.8676
Running experiment with seed=2:
 - alpha=0.5, K=22, layers=2, hidden=256, out=128
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.19582571123827155
 - ratio=0.0944447007633662, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.2990, LPL: 1.3646, Contrastive: 0.0395
Epoch 50, Loss: 0.2673, LPL: 1.3646, Contrastive: 0.0001
Epoch 100, Loss: 3.8831, LPL: 19.8288, Contrastive: 0.0002
 - Metrics: Accuracy=0.9179, F1=0.7842, Recall=0.7076, Precision=0.8794
Running experiment with seed=3:
 - alpha=0.5, K=22, la

[I 2025-02-27 03:19:16,005] Trial 0 finished with value: 0.7765669506390663 and parameters: {'K': 22, 'layers': 2, 'hidden_channels': 256, 'out_channels': 128, 'lpl_weight': 0.19582571123827155, 'ratio': 0.0944447007633662, 'aggregation': 'mean', 'treatment': 'removal'}. Best is trial 0 with value: 0.7765669506390663.


 - Metrics: Accuracy=0.9146, F1=0.7735, Recall=0.6919, Precision=0.8770
Done. Results written to citeseer_experimentations\citeseer_scar_learnable_params_2702031737.csv.
Average F1 over 5 seeds: 0.7766 ± 0.0075
Running experiment with seed=1:
 - alpha=0.5, K=16, layers=2, hidden=256, out=128
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5089002440944113
 - ratio=0.08089859476666938, pos_weight=1, aggregation=sum, treatment=relabeling
Epoch 0, Loss: 0.6547, LPL: 1.2065, Contrastive: 0.0829
Epoch 50, Loss: 0.6140, LPL: 1.2065, Contrastive: 0.0000
Epoch 100, Loss: 7.3070, LPL: 14.3583, Contrastive: 0.0002
 - Metrics: Accuracy=0.9128, F1=0.7755, Recall=0.7147, Precision=0.8477
Running experiment with seed=2:
 - alpha=0.5, K=16, layers=2, hidden=256, out=128
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.5089002440944113
 - ratio=0.08089859476666938, pos_weight=1, aggregation=sum, treatment=relabeling
Epoch 0, Loss: 0.5256, LPL: 0.8796, Contrastive: 0.1588
Epoch 50, Loss: 0.4476, LPL

[I 2025-02-27 03:20:50,413] Trial 1 finished with value: 0.778328173374613 and parameters: {'K': 16, 'layers': 2, 'hidden_channels': 256, 'out_channels': 128, 'lpl_weight': 0.5089002440944113, 'ratio': 0.08089859476666938, 'aggregation': 'sum', 'treatment': 'relabeling'}. Best is trial 1 with value: 0.778328173374613.


...

 - Metrics: Accuracy=0.9267, F1=0.8270, Recall=0.8317, Precision=0.8223
Done. Results written to citeseer_experimentations\citeseer_scar_learnable_params_2702075431.csv.
Average F1 over 5 seeds: 0.8283 ± 0.0071
Running experiment with seed=1:
 - alpha=0.5, K=22, layers=1, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.9583366731096798
 - ratio=0.22675045883371295, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 1.3934, LPL: 1.4537, Contrastive: 0.0053
Epoch 50, Loss: 1.3932, LPL: 1.4537, Contrastive: 0.0000
 - Metrics: Accuracy=0.9008, F1=0.7712, Recall=0.7932, Precision=0.7503
Running experiment with seed=2:
 - alpha=0.5, K=22, layers=1, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.9583366731096798
 - ratio=0.22675045883371295, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 1.3563, LPL: 1.4149, Contrastive: 0.0080
 - Metrics: Accuracy=0.9005, F1=0.7747, Recall=0.8117, Precision=0.7409
Running experiment

[I 2025-02-27 07:57:04,385] Trial 198 finished with value: 0.7548777075656057 and parameters: {'K': 22, 'layers': 1, 'hidden_channels': 128, 'out_channels': 256, 'lpl_weight': 0.9583366731096798, 'ratio': 0.22675045883371295, 'aggregation': 'mean', 'treatment': 'removal'}. Best is trial 171 with value: 0.8331855982991756.


 - Metrics: Accuracy=0.8909, F1=0.7438, Recall=0.7518, Precision=0.7360
Done. Results written to citeseer_experimentations\citeseer_scar_learnable_params_2702075559.csv.
Average F1 over 5 seeds: 0.7549 ± 0.0150
Running experiment with seed=1:
 - alpha=0.5, K=21, layers=1, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.9208046169406767
 - ratio=0.1970969393188106, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 1.2905, LPL: 1.4000, Contrastive: 0.0172
Epoch 50, Loss: 1.2891, LPL: 1.4000, Contrastive: 0.0000
 - Metrics: Accuracy=0.9270, F1=0.8280, Recall=0.8345, Precision=0.8216
Running experiment with seed=2:
 - alpha=0.5, K=21, layers=1, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.9208046169406767
 - ratio=0.1970969393188106, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 1.2382, LPL: 1.3429, Contrastive: 0.0211
Epoch 50, Loss: 1.2366, LPL: 1.3429, Contrastive: 0.0000
 - Metrics: Accuracy=0.9267, F1=0.8

[I 2025-02-27 07:58:34,837] Trial 199 finished with value: 0.8219273652375936 and parameters: {'K': 21, 'layers': 1, 'hidden_channels': 256, 'out_channels': 256, 'lpl_weight': 0.9208046169406767, 'ratio': 0.1970969393188106, 'aggregation': 'mean', 'treatment': 'removal'}. Best is trial 171 with value: 0.8331855982991756.


 - Metrics: Accuracy=0.9258, F1=0.8224, Recall=0.8160, Precision=0.8290
Done. Results written to citeseer_experimentations\citeseer_scar_learnable_params_2702075704.csv.
Average F1 over 5 seeds: 0.8219 ± 0.0054
Best trial:
  Average F1: 0.8331855982991756
  Best parameters:
    K: 22
    layers: 1
    hidden_channels: 256
    out_channels: 256
    lpl_weight: 0.977604520309747
    ratio: 0.21286340862957137
    aggregation: mean
    treatment: removal


### Hyperparameter Optimization Citeseer
#### SAR 

In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "citeseer",      
        "mechanism": "SAR",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 15, 25),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0.1, 0.5),
        "margin": 0.5,
        "lpl_weight": trial.suggest_float("lpl_weight", 0.1, 1.0),
        "ratio": trial.suggest_float("ratio", 0.05, 0.25),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ["sum", "mean"]),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "seeds": 5,
        "output_csv": "citeseer_sar_learnable_params.csv"
    }
    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=250)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-02-25 14:32:57,648] A new study created in memory with name: no-name-1ddade82-00f7-415f-bdcf-cb46c14bcf29


Running experiment with seed=1:
 - alpha=0.5, K=25, layers=2, hidden=256, out=128
 - norm=None, dropout=0.23522024944013312, margin=0.5, lpl_weight=0.974899320327853
 - ratio=0.06744147417045919, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 1.4624, LPL: 1.4986, Contrastive: 0.0574
Epoch 50, Loss: 1.4610, LPL: 1.4986, Contrastive: 0.0001
 - Metrics: Accuracy=0.9083, F1=0.7417, Recall=0.6248, Precision=0.9125
Running experiment with seed=2:
 - alpha=0.5, K=25, layers=2, hidden=256, out=128
 - norm=None, dropout=0.23522024944013312, margin=0.5, lpl_weight=0.974899320327853
 - ratio=0.06744147417045919, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 1.4089, LPL: 1.4432, Contrastive: 0.0746
Epoch 50, Loss: 1.4070, LPL: 1.4432, Contrastive: 0.0001
 - Metrics: Accuracy=0.9059, F1=0.7345, Recall=0.6177, Precision=0.9059
Running experiment with seed=3:
 - alpha=0.5, K=25, layers=2, hidden=256, out=128
 - norm=None, dropout=0.23522024944013312, margin=0.5, l

[I 2025-02-25 14:34:25,813] Trial 0 finished with value: 0.7311878110033405 and parameters: {'K': 25, 'layers': 2, 'hidden_channels': 256, 'out_channels': 128, 'dropout': 0.23522024944013312, 'lpl_weight': 0.974899320327853, 'ratio': 0.06744147417045919, 'aggregation': 'mean'}. Best is trial 0 with value: 0.7311878110033405.


 - Metrics: Accuracy=0.9089, F1=0.7421, Recall=0.6220, Precision=0.9198
Done. Results written to citeseer_experimentations\citeseer_sar_learnable_params_2502143257.csv.
Average F1 over 5 seeds: 0.7312 ± 0.0155
Running experiment with seed=1:
 - alpha=0.5, K=20, layers=1, hidden=128, out=256
 - norm=None, dropout=0.12058702394771532, margin=0.5, lpl_weight=0.7473275459102271
 - ratio=0.16995449518467848, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 1.0217, LPL: 1.3484, Contrastive: 0.0554
Epoch 50, Loss: 1.0077, LPL: 1.3484, Contrastive: 0.0001
Epoch 100, Loss: 13.4780, LPL: 18.0349, Contrastive: 0.0001
 - Metrics: Accuracy=0.9273, F1=0.8223, Recall=0.7989, Precision=0.8472
Running experiment with seed=2:
 - alpha=0.5, K=20, layers=1, hidden=128, out=256
 - norm=None, dropout=0.12058702394771532, margin=0.5, lpl_weight=0.7473275459102271
 - ratio=0.16995449518467848, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 1.0404, LPL: 1.3740, Contrastive: 0.05

[I 2025-02-25 14:35:55,466] Trial 1 finished with value: 0.811875750009959 and parameters: {'K': 20, 'layers': 1, 'hidden_channels': 128, 'out_channels': 256, 'dropout': 0.12058702394771532, 'lpl_weight': 0.7473275459102271, 'ratio': 0.16995449518467848, 'aggregation': 'sum'}. Best is trial 1 with value: 0.811875750009959.


...

 - Metrics: Accuracy=0.9261, F1=0.8250, Recall=0.8274, Precision=0.8227
Done. Results written to citeseer_experimentations\citeseer_sar_learnable_params_2502205353.csv.
Average F1 over 5 seeds: 0.8236 ± 0.0025
Running experiment with seed=1:
 - alpha=0.5, K=20, layers=1, hidden=256, out=256
 - norm=None, dropout=0.17219788846963627, margin=0.5, lpl_weight=0.9674423849705379
 - ratio=0.17954312793956098, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 1.2752, LPL: 1.3163, Contrastive: 0.0538
 - Metrics: Accuracy=0.9339, F1=0.8408, Recall=0.8288, Precision=0.8532
Running experiment with seed=2:
 - alpha=0.5, K=20, layers=1, hidden=256, out=256
 - norm=None, dropout=0.17219788846963627, margin=0.5, lpl_weight=0.9674423849705379
 - ratio=0.17954312793956098, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 1.2541, LPL: 1.2941, Contrastive: 0.0665
Epoch 50, Loss: 1.2520, LPL: 1.2941, Contrastive: 0.0001
 - Metrics: Accuracy=0.9273, F1=0.8210, Recall=0.7917, Pr

[I 2025-02-25 20:56:08,060] Trial 248 finished with value: 0.8266822626148894 and parameters: {'K': 20, 'layers': 1, 'hidden_channels': 256, 'out_channels': 256, 'dropout': 0.17219788846963627, 'lpl_weight': 0.9674423849705379, 'ratio': 0.17954312793956098, 'aggregation': 'sum'}. Best is trial 205 with value: 0.8318308688180981.


 - Metrics: Accuracy=0.9288, F1=0.8286, Recall=0.8174, Precision=0.8402
Done. Results written to citeseer_experimentations\citeseer_sar_learnable_params_2502205454.csv.
Average F1 over 5 seeds: 0.8267 ± 0.0085
Running experiment with seed=1:
 - alpha=0.5, K=22, layers=1, hidden=256, out=128
 - norm=None, dropout=0.17240479214242987, margin=0.5, lpl_weight=0.987133853121539
 - ratio=0.20515910504232293, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 1.3564, LPL: 1.3734, Contrastive: 0.0512
Epoch 50, Loss: 1.3557, LPL: 1.3734, Contrastive: 0.0001
 - Metrics: Accuracy=0.9276, F1=0.8257, Recall=0.8146, Precision=0.8372
Running experiment with seed=2:
 - alpha=0.5, K=22, layers=1, hidden=256, out=128
 - norm=None, dropout=0.17240479214242987, margin=0.5, lpl_weight=0.987133853121539
 - ratio=0.20515910504232293, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 1.2656, LPL: 1.2813, Contrastive: 0.0611
 - Metrics: Accuracy=0.9182, F1=0.8035, Recall=0.7932, Prec

[I 2025-02-25 20:57:08,834] Trial 249 finished with value: 0.8112575280093577 and parameters: {'K': 22, 'layers': 1, 'hidden_channels': 256, 'out_channels': 128, 'dropout': 0.17240479214242987, 'lpl_weight': 0.987133853121539, 'ratio': 0.20515910504232293, 'aggregation': 'sum'}. Best is trial 205 with value: 0.8318308688180981.


 - Metrics: Accuracy=0.9255, F1=0.8229, Recall=0.8217, Precision=0.8240
Done. Results written to citeseer_experimentations\citeseer_sar_learnable_params_2502205608.csv.
Average F1 over 5 seeds: 0.8113 ± 0.0137
Best trial:
  Average F1: 0.8318308688180981
  Best parameters:
    K: 20
    layers: 1
    hidden_channels: 256
    out_channels: 256
    dropout: 0.15710913243299005
    lpl_weight: 0.9822721262276471
    ratio: 0.17392076895103395
    aggregation: sum


### Hyperparameter Optimization Cora
#### SCAR 

In [5]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "cora",      
        "mechanism": "SCAR",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 25, 35),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0.1, 0.5),
        "margin": 0.5,
        "lpl_weight": trial.suggest_float("lpl_weight", 0.1, 1.0),
        "ratio": trial.suggest_float("ratio", 0.05, 0.5),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ["sum", "mean"]),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "seeds": 5,
        "output_csv": "cora_scar_learnable_params.csv"
    }
    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=150)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-02-27 07:58:34,876] A new study created in memory with name: no-name-a2fde53a-e921-4f95-9557-18f40cb1abd7


Running experiment with seed=1:
 - alpha=0.5, K=25, layers=2, hidden=128, out=128
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.7762541282543719
 - ratio=0.21900407506784975, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.9471, LPL: 1.2167, Contrastive: 0.0119
Epoch 50, Loss: 0.9445, LPL: 1.2167, Contrastive: 0.0000
Epoch 100, Loss: 16.8258, LPL: 21.6756, Contrastive: 0.0000
 - Metrics: Accuracy=0.8804, F1=0.7790, Recall=0.6980, Precision=0.8812
Running experiment with seed=2:
 - alpha=0.5, K=25, layers=2, hidden=128, out=128
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.7762541282543719
 - ratio=0.21900407506784975, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.9360, LPL: 1.2003, Contrastive: 0.0191
Epoch 50, Loss: 0.9317, LPL: 1.2003, Contrastive: 0.0001
Epoch 100, Loss: 16.8259, LPL: 21.6758, Contrastive: 0.0000
 - Metrics: Accuracy=0.8759, F1=0.7742, Recall=0.7042, Precision=0.8597
Running experiment with seed=3:
 - alpha=0.5, K=25, 

[I 2025-02-27 07:59:30,762] Trial 0 finished with value: 0.7735379977153378 and parameters: {'K': 25, 'layers': 2, 'hidden_channels': 128, 'out_channels': 128, 'lpl_weight': 0.7762541282543719, 'ratio': 0.21900407506784975, 'aggregation': 'mean', 'treatment': 'removal'}. Best is trial 0 with value: 0.7735379977153378.


 - Metrics: Accuracy=0.8752, F1=0.7636, Recall=0.6675, Precision=0.8922
Done. Results written to cora_experimentations\cora_scar_learnable_params_2702075834.csv.
Average F1 over 5 seeds: 0.7735 ± 0.0068
Running experiment with seed=1:
 - alpha=0.5, K=28, layers=1, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.8514175103209571
 - ratio=0.4731724898085401, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 1.2287, LPL: 1.4423, Contrastive: 0.0047
Epoch 50, Loss: 1.2280, LPL: 1.4423, Contrastive: 0.0000
 - Metrics: Accuracy=0.8549, F1=0.7865, Recall=0.8851, Precision=0.7077
Running experiment with seed=2:
 - alpha=0.5, K=28, layers=1, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.8514175103209571
 - ratio=0.4731724898085401, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 1.2004, LPL: 1.4079, Contrastive: 0.0108
Epoch 50, Loss: 1.1988, LPL: 1.4079, Contrastive: 0.0000
 - Metrics: Accuracy=0.8401, F1=0.7622, Rec

[I 2025-02-27 08:00:19,855] Trial 1 finished with value: 0.7743360493419689 and parameters: {'K': 28, 'layers': 1, 'hidden_channels': 128, 'out_channels': 256, 'lpl_weight': 0.8514175103209571, 'ratio': 0.4731724898085401, 'aggregation': 'mean', 'treatment': 'removal'}. Best is trial 1 with value: 0.7743360493419689.


...

 - Metrics: Accuracy=0.8977, F1=0.8135, Recall=0.7384, Precision=0.9055
Done. Results written to cora_experimentations\cora_scar_learnable_params_2702105245.csv.
Average F1 over 5 seeds: 0.8508 ± 0.0193
Running experiment with seed=1:
 - alpha=0.5, K=35, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.11892636628965142
 - ratio=0.24751417070015239, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.1695, LPL: 1.2622, Contrastive: 0.0219
Epoch 50, Loss: 0.1501, LPL: 1.2622, Contrastive: 0.0000
Epoch 100, Loss: 3.2731, LPL: 27.5215, Contrastive: 0.0001
 - Metrics: Accuracy=0.9313, F1=0.8877, Recall=0.8985, Precision=0.8771
Running experiment with seed=2:
 - alpha=0.5, K=35, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.11892636628965142
 - ratio=0.24751417070015239, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.1809, LPL: 1.2691, Contrastive: 0.0340
Epoch 50, Loss: 0.1510, LPL: 1.2691, Co

[I 2025-02-27 10:55:38,450] Trial 148 finished with value: 0.8877295638630704 and parameters: {'K': 35, 'layers': 2, 'hidden_channels': 256, 'out_channels': 256, 'lpl_weight': 0.11892636628965142, 'ratio': 0.24751417070015239, 'aggregation': 'sum', 'treatment': 'removal'}. Best is trial 82 with value: 0.8896956718424228.


 - Metrics: Accuracy=0.9346, F1=0.8909, Recall=0.8839, Precision=0.8981
Done. Results written to cora_experimentations\cora_scar_learnable_params_2702105407.csv.
Average F1 over 5 seeds: 0.8877 ± 0.0065
Running experiment with seed=1:
 - alpha=0.5, K=35, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.12485436129167085
 - ratio=0.2603645539829617, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.1760, LPL: 1.2656, Contrastive: 0.0206
Epoch 50, Loss: 0.1580, LPL: 1.2656, Contrastive: 0.0000
 - Metrics: Accuracy=0.9250, F1=0.8792, Recall=0.9034, Precision=0.8563
Running experiment with seed=2:
 - alpha=0.5, K=35, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.12485436129167085
 - ratio=0.2603645539829617, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.1889, LPL: 1.2755, Contrastive: 0.0339
Epoch 50, Loss: 0.1593, LPL: 1.2755, Contrastive: 0.0000
Epoch 100, Loss: 3.4366, LPL: 27.5243, Cont

[I 2025-02-27 10:56:59,221] Trial 149 finished with value: 0.8810961525247626 and parameters: {'K': 35, 'layers': 2, 'hidden_channels': 256, 'out_channels': 256, 'lpl_weight': 0.12485436129167085, 'ratio': 0.2603645539829617, 'aggregation': 'sum', 'treatment': 'removal'}. Best is trial 82 with value: 0.8896956718424228.


 - Metrics: Accuracy=0.9343, F1=0.8905, Recall=0.8851, Precision=0.8960
Done. Results written to cora_experimentations\cora_scar_learnable_params_2702105538.csv.
Average F1 over 5 seeds: 0.8811 ± 0.0095
Best trial:
  Average F1: 0.8896956718424228
  Best parameters:
    K: 35
    layers: 2
    hidden_channels: 256
    out_channels: 256
    lpl_weight: 0.21270556940392277
    ratio: 0.24776858031259816
    aggregation: sum
    treatment: removal


### Hyperparameter Optimization Cora
#### SAR 

In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "cora",      
        "mechanism": "SAR",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 25, 35),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0.1, 0.5),
        "margin": 0.5,
        "lpl_weight": trial.suggest_float("lpl_weight", 0.1, 1.0),
        "ratio": trial.suggest_float("ratio", 0.05, 0.5),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ["sum", "mean"]),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "seeds": 5,
        "output_csv": "cora_sar_learnable_params.csv"
    }
    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=100)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-02-25 22:57:34,332] A new study created in memory with name: no-name-418c82fb-88c1-4c89-a998-ddfef6c23497


Running experiment with seed=1:
 - alpha=0.5, K=34, layers=1, hidden=128, out=256
 - norm=None, dropout=0.49055583386404333, margin=0.5, lpl_weight=0.849910877780626
 - ratio=0.39276826346984645, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 1.1812, LPL: 1.3833, Contrastive: 0.0367
Epoch 50, Loss: 1.1757, LPL: 1.3833, Contrastive: 0.0002
Epoch 100, Loss: 23.2682, LPL: 27.3772, Contrastive: 0.0000
 - Metrics: Accuracy=0.8874, F1=0.8345, Recall=0.9401, Precision=0.7502
Running experiment with seed=2:
 - alpha=0.5, K=34, layers=1, hidden=128, out=256
 - norm=None, dropout=0.49055583386404333, margin=0.5, lpl_weight=0.849910877780626
 - ratio=0.39276826346984645, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 1.2497, LPL: 1.4661, Contrastive: 0.0240
Epoch 50, Loss: 1.2461, LPL: 1.4661, Contrastive: 0.0001
Epoch 100, Loss: 23.2726, LPL: 27.3824, Contrastive: 0.0000
 - Metrics: Accuracy=0.8708, F1=0.8138, Recall=0.9352, Precision=0.7203
Running experiment w

[I 2025-02-25 22:58:44,379] Trial 0 finished with value: 0.8161186858496444 and parameters: {'K': 34, 'layers': 1, 'hidden_channels': 128, 'out_channels': 256, 'dropout': 0.49055583386404333, 'lpl_weight': 0.849910877780626, 'ratio': 0.39276826346984645, 'aggregation': 'sum'}. Best is trial 0 with value: 0.8161186858496444.


 - Metrics: Accuracy=0.8733, F1=0.8161, Recall=0.9303, Precision=0.7268
Done. Results written to cora_experimentations\cora_sar_learnable_params_2502225734.csv.
Average F1 over 5 seeds: 0.8161 ± 0.0100
Running experiment with seed=1:
 - alpha=0.5, K=33, layers=1, hidden=128, out=256
 - norm=None, dropout=0.4501901340387927, margin=0.5, lpl_weight=0.8489543245097706
 - ratio=0.3039978353757287, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 1.1177, LPL: 1.3089, Contrastive: 0.0432
Epoch 50, Loss: 1.1112, LPL: 1.3089, Contrastive: 0.0002
Epoch 100, Loss: 23.0888, LPL: 27.1968, Contrastive: 0.0000
 - Metrics: Accuracy=0.9125, F1=0.8624, Recall=0.9083, Precision=0.8210
Running experiment with seed=2:
 - alpha=0.5, K=33, layers=1, hidden=128, out=256
 - norm=None, dropout=0.4501901340387927, margin=0.5, lpl_weight=0.8489543245097706
 - ratio=0.3039978353757287, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 1.1972, LPL: 1.4045, Contrastive: 0.0321
Epoch 50,

[I 2025-02-25 22:59:54,014] Trial 1 finished with value: 0.8469580084601877 and parameters: {'K': 33, 'layers': 1, 'hidden_channels': 128, 'out_channels': 256, 'dropout': 0.4501901340387927, 'lpl_weight': 0.8489543245097706, 'ratio': 0.3039978353757287, 'aggregation': 'sum'}. Best is trial 1 with value: 0.8469580084601877.


...

 - Metrics: Accuracy=0.9369, F1=0.8970, Recall=0.9108, Precision=0.8837
Done. Results written to cora_experimentations\cora_sar_learnable_params_2602004534.csv.
Average F1 over 5 seeds: 0.8911 ± 0.0042
Running experiment with seed=1:
 - alpha=0.5, K=28, layers=2, hidden=256, out=256
 - norm=None, dropout=0.390287854449124, margin=0.5, lpl_weight=0.2174863901173385
 - ratio=0.2657194959435572, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.3018, LPL: 1.2039, Contrastive: 0.0511
Epoch 50, Loss: 0.2619, LPL: 1.2039, Contrastive: 0.0001
Epoch 100, Loss: 5.2438, LPL: 24.1106, Contrastive: 0.0001
 - Metrics: Accuracy=0.9365, F1=0.8937, Recall=0.8839, Precision=0.9038
Running experiment with seed=2:
 - alpha=0.5, K=28, layers=2, hidden=256, out=256
 - norm=None, dropout=0.390287854449124, margin=0.5, lpl_weight=0.2174863901173385
 - ratio=0.2657194959435572, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.3169, LPL: 1.2946, Contrastive: 0.0452
Epoch 50, Lo

[I 2025-02-26 00:47:58,645] Trial 98 finished with value: 0.8818389649608959 and parameters: {'K': 28, 'layers': 2, 'hidden_channels': 256, 'out_channels': 256, 'dropout': 0.390287854449124, 'lpl_weight': 0.2174863901173385, 'ratio': 0.2657194959435572, 'aggregation': 'sum'}. Best is trial 93 with value: 0.8936709270447185.


 - Metrics: Accuracy=0.9332, F1=0.8906, Recall=0.9010, Precision=0.8805
Done. Results written to cora_experimentations\cora_sar_learnable_params_2602004649.csv.
Average F1 over 5 seeds: 0.8818 ± 0.0114
Running experiment with seed=1:
 - alpha=0.5, K=28, layers=1, hidden=256, out=256
 - norm=None, dropout=0.4356067933402399, margin=0.5, lpl_weight=0.2489609832902156
 - ratio=0.2729534670003436, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.3381, LPL: 1.2118, Contrastive: 0.0484
Epoch 50, Loss: 0.3017, LPL: 1.2118, Contrastive: 0.0001
Epoch 100, Loss: 6.0027, LPL: 24.1110, Contrastive: 0.0000
 - Metrics: Accuracy=0.9346, F1=0.8911, Recall=0.8851, Precision=0.8971
Running experiment with seed=2:
 - alpha=0.5, K=28, layers=1, hidden=256, out=256
 - norm=None, dropout=0.4356067933402399, margin=0.5, lpl_weight=0.2489609832902156
 - ratio=0.2729534670003436, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.3562, LPL: 1.2977, Contrastive: 0.0441
Epoch 50, 

[I 2025-02-26 00:49:11,156] Trial 99 finished with value: 0.886563012960574 and parameters: {'K': 28, 'layers': 1, 'hidden_channels': 256, 'out_channels': 256, 'dropout': 0.4356067933402399, 'lpl_weight': 0.2489609832902156, 'ratio': 0.2729534670003436, 'aggregation': 'sum'}. Best is trial 93 with value: 0.8936709270447185.


 - Metrics: Accuracy=0.9317, F1=0.8881, Recall=0.8973, Precision=0.8790
Done. Results written to cora_experimentations\cora_sar_learnable_params_2602004758.csv.
Average F1 over 5 seeds: 0.8866 ± 0.0035
Best trial:
  Average F1: 0.8936709270447185
  Best parameters:
    K: 28
    layers: 1
    hidden_channels: 256
    out_channels: 256
    dropout: 0.39653137239313224
    lpl_weight: 0.4331932670956203
    ratio: 0.2534043950024391
    aggregation: sum


### Hyperparameter Optimization Pubmed
#### SCAR 

In [6]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "pubmed",      
        "mechanism": "SCAR",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 25, 35),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0.1, 0.5),
        "margin": 0.5,
        "lpl_weight": trial.suggest_float("lpl_weight", 0.1, 1.0),
        "ratio": trial.suggest_float("ratio", 0.05, 0.5),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ["sum", "mean"]),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "seeds": 5,
        "output_csv": "pubmed_scar_learnable_params.csv"
    }
    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=50)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-02-27 10:56:59,283] A new study created in memory with name: no-name-bb3a982f-550e-47dd-8191-f80f1417df00


Running experiment with seed=1:
 - alpha=0.5, K=30, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.6394688104117316
 - ratio=0.42337181198708806, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 1.1766, LPL: 1.8214, Contrastive: 0.0330
 - Metrics: Accuracy=0.8487, F1=0.8287, Recall=0.9163, Precision=0.7563
Running experiment with seed=2:
 - alpha=0.5, K=30, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.6394688104117316
 - ratio=0.42337181198708806, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 1.1492, LPL: 1.7775, Contrastive: 0.0348
 - Metrics: Accuracy=0.8483, F1=0.8293, Recall=0.9229, Precision=0.7529
Running experiment with seed=3:
 - alpha=0.5, K=30, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.6394688104117316
 - ratio=0.42337181198708806, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 1.1811, LPL: 1.8284, Contrastive: 0.0329
 - M

[I 2025-02-27 10:59:54,509] Trial 0 finished with value: 0.8278198833805558 and parameters: {'K': 30, 'layers': 2, 'hidden_channels': 256, 'out_channels': 256, 'lpl_weight': 0.6394688104117316, 'ratio': 0.42337181198708806, 'aggregation': 'sum', 'treatment': 'removal'}. Best is trial 0 with value: 0.8278198833805558.


 - Metrics: Accuracy=0.8394, F1=0.8196, Recall=0.9133, Precision=0.7433
Done. Results written to pubmed_experimentations\pubmed_scar_learnable_params_2702105659.csv.
Average F1 over 5 seeds: 0.8278 ± 0.0043
Running experiment with seed=1:
 - alpha=0.5, K=35, layers=1, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.1320945709856277
 - ratio=0.16662606200455948, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.2300, LPL: 1.4832, Contrastive: 0.0392
Epoch 50, Loss: 0.1961, LPL: 1.4832, Contrastive: 0.0002
Epoch 100, Loss: 3.4908, LPL: 26.4250, Contrastive: 0.0002
 - Metrics: Accuracy=0.8896, F1=0.8517, Recall=0.7935, Precision=0.9191
Running experiment with seed=2:
 - alpha=0.5, K=35, layers=1, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.1320945709856277
 - ratio=0.16662606200455948, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.2308, LPL: 1.4810, Contrastive: 0.0406
Epoch 50, Loss: 0.1958, LPL: 1.4810, 

[I 2025-02-27 11:03:36,339] Trial 1 finished with value: 0.8488196211492356 and parameters: {'K': 35, 'layers': 1, 'hidden_channels': 128, 'out_channels': 256, 'lpl_weight': 0.1320945709856277, 'ratio': 0.16662606200455948, 'aggregation': 'sum', 'treatment': 'removal'}. Best is trial 1 with value: 0.8488196211492356.


...

 - Metrics: Accuracy=0.9074, F1=0.8813, Recall=0.8604, Precision=0.9032
Done. Results written to pubmed_experimentations\pubmed_scar_learnable_params_2702133611.csv.
Average F1 over 5 seeds: 0.8847 ± 0.0021
Running experiment with seed=1:
 - alpha=0.5, K=28, layers=1, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.24333152109533995
 - ratio=0.18899829275789515, pos_weight=1, aggregation=mean, treatment=relabeling
Epoch 0, Loss: 0.2093, LPL: 0.8589, Contrastive: 0.0005
Epoch 50, Loss: 0.2091, LPL: 0.8589, Contrastive: 0.0001
Epoch 100, Loss: 5.4263, LPL: 22.2998, Contrastive: 0.0000
 - Metrics: Accuracy=0.9096, F1=0.8800, Recall=0.8295, Precision=0.9370
Running experiment with seed=2:
 - alpha=0.5, K=28, layers=1, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.24333152109533995
 - ratio=0.18899829275789515, pos_weight=1, aggregation=mean, treatment=relabeling
Epoch 0, Loss: 0.2088, LPL: 0.8566, Contrastive: 0.0005
Epoch 50, Loss: 0.2086, LPL

[I 2025-02-27 13:44:55,415] Trial 48 finished with value: 0.8796266067852242 and parameters: {'K': 28, 'layers': 1, 'hidden_channels': 256, 'out_channels': 256, 'lpl_weight': 0.24333152109533995, 'ratio': 0.18899829275789515, 'aggregation': 'mean', 'treatment': 'relabeling'}. Best is trial 42 with value: 0.8850405397438378.


 - Metrics: Accuracy=0.9072, F1=0.8771, Recall=0.8292, Precision=0.9309
Done. Results written to pubmed_experimentations\pubmed_scar_learnable_params_2702134032.csv.
Average F1 over 5 seeds: 0.8796 ± 0.0017
Running experiment with seed=1:
 - alpha=0.5, K=31, layers=1, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.3151376459144398
 - ratio=0.32135464643909073, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.5294, LPL: 1.5856, Contrastive: 0.0434
 - Metrics: Accuracy=0.8789, F1=0.8530, Recall=0.8799, Precision=0.8277
Running experiment with seed=2:
 - alpha=0.5, K=31, layers=1, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.3151376459144398
 - ratio=0.32135464643909073, pos_weight=1, aggregation=sum, treatment=removal
Epoch 0, Loss: 0.5199, LPL: 1.5517, Contrastive: 0.0452
 - Metrics: Accuracy=0.8794, F1=0.8541, Recall=0.8837, Precision=0.8264
Running experiment with seed=3:
 - alpha=0.5, K=31, layers=1, hidden=256, out=256

[I 2025-02-27 13:47:43,462] Trial 49 finished with value: 0.8515187737525235 and parameters: {'K': 31, 'layers': 1, 'hidden_channels': 256, 'out_channels': 256, 'lpl_weight': 0.3151376459144398, 'ratio': 0.32135464643909073, 'aggregation': 'sum', 'treatment': 'removal'}. Best is trial 42 with value: 0.8850405397438378.


 - Metrics: Accuracy=0.8723, F1=0.8457, Recall=0.8763, Precision=0.8172
Done. Results written to pubmed_experimentations\pubmed_scar_learnable_params_2702134455.csv.
Average F1 over 5 seeds: 0.8515 ± 0.0030
Best trial:
  Average F1: 0.8850405397438378
  Best parameters:
    K: 27
    layers: 1
    hidden_channels: 256
    out_channels: 128
    lpl_weight: 0.23715426467656936
    ratio: 0.22179057400780028
    aggregation: mean
    treatment: relabeling


### Hyperparameter Optimization Pubmed
#### SAR 

In [ ]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "pubmed",      
        "mechanism": "SAR",
        "train_pct": 0.5,
        "alpha": 0.5,
        "K": trial.suggest_int("K", 25, 35),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [64, 128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [64, 128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0.1, 0.5),
        "margin": 0.5,
        "lpl_weight": trial.suggest_float("lpl_weight", 0.1, 1.0),
        "ratio": trial.suggest_float("ratio", 0.05, 0.5),
        "pos_weight": 1,
        "aggregation": trial.suggest_categorical("aggregation", ["sum", "mean"]),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "seeds": 5,
        "output_csv": "pubmed_sar_learnable_params.csv"
    }
    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=100)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-02-26 03:23:53,936] A new study created in memory with name: no-name-7f4cbf8f-985f-4bdf-acf7-67c58479d826


Running experiment with seed=1:
 - alpha=0.5, K=29, layers=2, hidden=128, out=128
 - norm=None, dropout=0.13019271568601654, margin=0.5, lpl_weight=0.9617526580395241
 - ratio=0.4686918535680597, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 1.5174, LPL: 1.5777, Contrastive: 0.0002
Epoch 50, Loss: 1.5174, LPL: 1.5777, Contrastive: 0.0001
 - Metrics: Accuracy=0.8649, F1=0.8455, Recall=0.9258, Precision=0.7780
Running experiment with seed=2:
 - alpha=0.5, K=29, layers=2, hidden=128, out=128
 - norm=None, dropout=0.13019271568601654, margin=0.5, lpl_weight=0.9617526580395241
 - ratio=0.4686918535680597, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 1.4896, LPL: 1.5488, Contrastive: 0.0002
Epoch 50, Loss: 1.4896, LPL: 1.5488, Contrastive: 0.0001
 - Metrics: Accuracy=0.8669, F1=0.8460, Recall=0.9154, Precision=0.7864
Running experiment with seed=3:
 - alpha=0.5, K=29, layers=2, hidden=128, out=128
 - norm=None, dropout=0.13019271568601654, margin=0.5, l

[I 2025-02-26 03:26:12,321] Trial 0 finished with value: 0.8441785629649907 and parameters: {'K': 29, 'layers': 2, 'hidden_channels': 128, 'out_channels': 128, 'dropout': 0.13019271568601654, 'lpl_weight': 0.9617526580395241, 'ratio': 0.4686918535680597, 'aggregation': 'mean'}. Best is trial 0 with value: 0.8441785629649907.


 - Metrics: Accuracy=0.8643, F1=0.8438, Recall=0.9177, Precision=0.7810
Done. Results written to pubmed_experimentations\pubmed_sar_learnable_params_2602032353.csv.
Average F1 over 5 seeds: 0.8442 ± 0.0014
Running experiment with seed=1:
 - alpha=0.5, K=35, layers=1, hidden=256, out=128
 - norm=None, dropout=0.2998522859023272, margin=0.5, lpl_weight=0.5609886595645283
 - ratio=0.4704598795028684, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.9071, LPL: 1.6155, Contrastive: 0.0019
Epoch 50, Loss: 0.9064, LPL: 1.6155, Contrastive: 0.0001
Epoch 100, Loss: 14.6880, LPL: 26.1823, Contrastive: 0.0000
 - Metrics: Accuracy=0.8733, F1=0.8544, Recall=0.9305, Precision=0.7897
Running experiment with seed=2:
 - alpha=0.5, K=35, layers=1, hidden=256, out=128
 - norm=None, dropout=0.2998522859023272, margin=0.5, lpl_weight=0.5609886595645283
 - ratio=0.4704598795028684, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.8935, LPL: 1.5912, Contrastive: 0.0019
Epo

[I 2025-02-26 03:29:46,339] Trial 1 finished with value: 0.853918427311636 and parameters: {'K': 35, 'layers': 1, 'hidden_channels': 256, 'out_channels': 128, 'dropout': 0.2998522859023272, 'lpl_weight': 0.5609886595645283, 'ratio': 0.4704598795028684, 'aggregation': 'mean'}. Best is trial 1 with value: 0.853918427311636.


...

 - Metrics: Accuracy=0.9031, F1=0.8767, Recall=0.8629, Precision=0.8910
Done. Results written to pubmed_experimentations\pubmed_sar_learnable_params_2602075820.csv.
Average F1 over 5 seeds: 0.8782 ± 0.0032
Running experiment with seed=1:
 - alpha=0.5, K=25, layers=2, hidden=128, out=256
 - norm=None, dropout=0.13511458111879743, margin=0.5, lpl_weight=0.2231074780696927
 - ratio=0.2698667009750044, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.3213, LPL: 1.4392, Contrastive: 0.0003
Epoch 50, Loss: 0.3212, LPL: 1.4392, Contrastive: 0.0001
Epoch 100, Loss: 4.5760, LPL: 20.5103, Contrastive: 0.0000
 - Metrics: Accuracy=0.9000, F1=0.8747, Recall=0.8739, Precision=0.8755
Running experiment with seed=2:
 - alpha=0.5, K=25, layers=2, hidden=128, out=256
 - norm=None, dropout=0.13511458111879743, margin=0.5, lpl_weight=0.2231074780696927
 - ratio=0.2698667009750044, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.3172, LPL: 1.4205, Contrastive: 0.0003
Ep

[I 2025-02-26 08:05:25,112] Trial 98 finished with value: 0.8754223410387084 and parameters: {'K': 25, 'layers': 2, 'hidden_channels': 128, 'out_channels': 256, 'dropout': 0.13511458111879743, 'lpl_weight': 0.2231074780696927, 'ratio': 0.2698667009750044, 'aggregation': 'mean'}. Best is trial 83 with value: 0.8798047359394902.


 - Metrics: Accuracy=0.8978, F1=0.8722, Recall=0.8728, Precision=0.8715
Done. Results written to pubmed_experimentations\pubmed_sar_learnable_params_2602080152.csv.
Average F1 over 5 seeds: 0.8754 ± 0.0036
Running experiment with seed=1:
 - alpha=0.5, K=25, layers=2, hidden=128, out=256
 - norm=None, dropout=0.11095177279889956, margin=0.5, lpl_weight=0.3240380657010947
 - ratio=0.26709136300274616, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.4664, LPL: 1.4388, Contrastive: 0.0003
Epoch 50, Loss: 0.4663, LPL: 1.4388, Contrastive: 0.0001
Epoch 100, Loss: 6.6475, LPL: 20.5144, Contrastive: 0.0000
 - Metrics: Accuracy=0.9016, F1=0.8767, Recall=0.8757, Precision=0.8777
Running experiment with seed=2:
 - alpha=0.5, K=25, layers=2, hidden=128, out=256
 - norm=None, dropout=0.11095177279889956, margin=0.5, lpl_weight=0.3240380657010947
 - ratio=0.26709136300274616, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 0.4593, LPL: 1.4168, Contrastive: 0.0003


[I 2025-02-26 08:08:59,181] Trial 99 finished with value: 0.8772450709674819 and parameters: {'K': 25, 'layers': 2, 'hidden_channels': 128, 'out_channels': 256, 'dropout': 0.11095177279889956, 'lpl_weight': 0.3240380657010947, 'ratio': 0.26709136300274616, 'aggregation': 'mean'}. Best is trial 83 with value: 0.8798047359394902.


 - Metrics: Accuracy=0.9014, F1=0.8762, Recall=0.8738, Precision=0.8787
Done. Results written to pubmed_experimentations\pubmed_sar_learnable_params_2602080525.csv.
Average F1 over 5 seeds: 0.8772 ± 0.0023
Best trial:
  Average F1: 0.8798047359394902
  Best parameters:
    K: 26
    layers: 2
    hidden_channels: 64
    out_channels: 64
    dropout: 0.1254611964387077
    lpl_weight: 0.24515372552362366
    ratio: 0.24282619680377082
    aggregation: mean


### Hyperparameter Optimization WikiCS
#### SCAR 

In [2]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "wiki-cs",      
        "mechanism": "SCAR",
        "train_pct": 0.5,
        "alpha": 0.5,#trial.suggest_float("alpha", 0.05, 1.0),
        "K": trial.suggest_int("K", 25, 45),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [ 128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0, 0.5),
        "margin": 0.5,
        "lpl_weight": trial.suggest_float("lpl_weight", 0.01, 1.0),
        "ratio": trial.suggest_float("ratio", 0.01, 0.5),
        "pos_weight": 1, #trial.suggest_float("pos_weight", 0.5, 2.0),
        "aggregation": trial.suggest_categorical("aggregation", ["sum", "mean"]),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "seeds": 5,
        "output_csv": "wikics_scar_learnable_params.csv"
    }
    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=150)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-02-26 19:45:00,628] A new study created in memory with name: no-name-0bd4e3f1-9f9b-49c3-9156-905f0c57f1df


Running experiment with seed=1:
 - alpha=0.5, K=34, layers=2, hidden=256, out=128
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.8413468772295923
 - ratio=0.19065735389208652, pos_weight=1, aggregation=sum, treatment=relabeling


ERROR:root:Anomaly detector error: ValueError('Input contains NaN.')


Epoch 0, Loss: nan, LPL: 19.3986, Contrastive: nan
 - Metrics: Accuracy=0.9010, F1=0.8069, Recall=0.9029, Precision=0.7293
Running experiment with seed=2:
 - alpha=0.5, K=34, layers=2, hidden=256, out=128
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.8413468772295923
 - ratio=0.19065735389208652, pos_weight=1, aggregation=sum, treatment=relabeling


ERROR:root:Anomaly detector error: ValueError('Input contains NaN.')


...

 - Metrics: Accuracy=0.9610, F1=0.9113, Recall=0.8746, Precision=0.9513
Done. Results written to wiki-cs_experimentations\wikics_scar_learnable_params_2702001745.csv.
Average F1 over 5 seeds: 0.9083 ± 0.0019
Running experiment with seed=1:
 - alpha=0.5, K=44, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.8491584757589823
 - ratio=0.1412085919188148, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 2.5241, LPL: 2.9724, Contrastive: 0.0001
 - Metrics: Accuracy=0.9583, F1=0.9075, Recall=0.8932, Precision=0.9222
Running experiment with seed=2:
 - alpha=0.5, K=44, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.8491584757589823
 - ratio=0.1412085919188148, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 2.5903, LPL: 3.0505, Contrastive: 0.0001
 - Metrics: Accuracy=0.9608, F1=0.9123, Recall=0.8914, Precision=0.9343
Running experiment with seed=3:
 - alpha=0.5, K=44, layers=2, hidden=256, out=25

[I 2025-02-27 00:21:45,040] Trial 148 finished with value: 0.9105055255759634 and parameters: {'K': 44, 'layers': 2, 'hidden_channels': 256, 'out_channels': 256, 'lpl_weight': 0.8491584757589823, 'ratio': 0.1412085919188148, 'aggregation': 'mean', 'treatment': 'removal'}. Best is trial 103 with value: 0.9127299443710456.


 - Metrics: Accuracy=0.9604, F1=0.9119, Recall=0.8947, Precision=0.9298
Done. Results written to wiki-cs_experimentations\wikics_scar_learnable_params_2702001945.csv.
Average F1 over 5 seeds: 0.9105 ± 0.0040
Running experiment with seed=1:
 - alpha=0.5, K=42, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.8749068457026103
 - ratio=0.13473276218312677, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 2.6041, LPL: 2.9765, Contrastive: 0.0001
 - Metrics: Accuracy=0.9590, F1=0.9087, Recall=0.8914, Precision=0.9267
Running experiment with seed=2:
 - alpha=0.5, K=42, layers=2, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.8749068457026103
 - ratio=0.13473276218312677, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 2.6683, LPL: 3.0498, Contrastive: 0.0001
 - Metrics: Accuracy=0.9614, F1=0.9142, Recall=0.8985, Precision=0.9304
Running experiment with seed=3:
 - alpha=0.5, K=42, layers=2, hidden=256, out=

[I 2025-02-27 00:23:43,707] Trial 149 finished with value: 0.9104442490190847 and parameters: {'K': 42, 'layers': 2, 'hidden_channels': 256, 'out_channels': 256, 'lpl_weight': 0.8749068457026103, 'ratio': 0.13473276218312677, 'aggregation': 'mean', 'treatment': 'removal'}. Best is trial 103 with value: 0.9127299443710456.


 - Metrics: Accuracy=0.9591, F1=0.9081, Recall=0.8813, Precision=0.9365
Done. Results written to wiki-cs_experimentations\wikics_scar_learnable_params_2702002145.csv.
Average F1 over 5 seeds: 0.9104 ± 0.0032
Best trial:
  Average F1: 0.9127299443710456
  Best parameters:
    K: 43
    layers: 2
    hidden_channels: 256
    out_channels: 256
    lpl_weight: 0.9714408789615457
    ratio: 0.1341089403291094
    aggregation: mean
    treatment: removal


### Hyperparameter Optimization WikiCS
#### SAR 

In [3]:
from train_NNIF_GNN import run_nnif_gnn_experiment
import optuna
from typing import Dict, Any

def objective(trial: optuna.trial.Trial) -> float:
    """
    Objective function for hyperparameter optimization using Optuna.
    It builds a parameter dictionary, calls the experiment function, and
    returns the average F1 score.
    """
    params: Dict[str, Any] = {
        "dataset_name": "wiki-cs",      
        "mechanism": "SAR",
        "train_pct": 0.5,
        "alpha": 0.5,#trial.suggest_float("alpha", 0.05, 1.0),
        "K": trial.suggest_int("K", 25, 45),
        "layers": trial.suggest_int("layers", 1, 2),
        "hidden_channels": trial.suggest_categorical("hidden_channels", [128, 256]),
        "out_channels": trial.suggest_categorical("out_channels", [ 128, 256]),
        "norm": None,
        "dropout": 0,#trial.suggest_float("dropout", 0, 0.5),
        "margin": 0.5,
        "lpl_weight": trial.suggest_float("lpl_weight", 0.01, 1.0),
        "ratio": trial.suggest_float("ratio", 0.01, 0.5),
        "pos_weight": 1, #trial.suggest_float("pos_weight", 0.5, 2.0),
        "aggregation": trial.suggest_categorical("aggregation", ["sum", "mean"]),
        "treatment": trial.suggest_categorical("treatment", ["removal", "relabeling"]),
        "seeds": 5,
        "output_csv": "wikics_sar_learnable_params.csv"
    }
    
    # Call the experiment function with these parameters.
    # run_nnif_gnn_experiment returns (avg_f1, std_f1)
    avg_f1, std_f1 = run_nnif_gnn_experiment(params)
    
    # We aim to maximize F1 score.
    return avg_f1

# Create an Optuna study to maximize the F1 score.
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=100)

# Print out the best hyperparameters and corresponding F1 score.
print("Best trial:")
trial = study.best_trial
print("  Average F1:", trial.value)
print("  Best parameters:")
for key, value in trial.params.items():
    print(f"    {key}: {value}")


[I 2025-02-27 00:23:43,749] A new study created in memory with name: no-name-0651131d-f94f-4263-836d-989f224364c3


Running experiment with seed=1:
 - alpha=0.5, K=40, layers=1, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.6561213398778427
 - ratio=0.1474974595079506, pos_weight=1, aggregation=sum, treatment=relabeling


ERROR:root:Anomaly detector error: ValueError('Input contains NaN.')


Epoch 0, Loss: nan, LPL: 19.9822, Contrastive: nan
 - Metrics: Accuracy=0.9242, F1=0.8401, Recall=0.8697, Precision=0.8124
Running experiment with seed=2:
 - alpha=0.5, K=40, layers=1, hidden=128, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.6561213398778427
 - ratio=0.1474974595079506, pos_weight=1, aggregation=sum, treatment=relabeling


ERROR:root:Anomaly detector error: ValueError('Input contains NaN.')


...

 - Metrics: Accuracy=0.9616, F1=0.9151, Recall=0.9037, Precision=0.9269
Done. Results written to wiki-cs_experimentations\wikics_sar_learnable_params_2702031150.csv.
Average F1 over 5 seeds: 0.9073 ± 0.0053
Running experiment with seed=1:
 - alpha=0.5, K=30, layers=1, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.6942151968028537
 - ratio=0.10619648424454017, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 2.0359, LPL: 2.9326, Contrastive: 0.0001
 - Metrics: Accuracy=0.9519, F1=0.8876, Recall=0.8302, Precision=0.9537
Running experiment with seed=2:
 - alpha=0.5, K=30, layers=1, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.6942151968028537
 - ratio=0.10619648424454017, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 2.0087, LPL: 2.8935, Contrastive: 0.0001
 - Metrics: Accuracy=0.9562, F1=0.8982, Recall=0.8429, Precision=0.9613
Running experiment with seed=3:
 - alpha=0.5, K=30, layers=1, hidden=256, out=2

[I 2025-02-27 03:15:41,895] Trial 98 finished with value: 0.8959296946004663 and parameters: {'K': 30, 'layers': 1, 'hidden_channels': 256, 'out_channels': 256, 'lpl_weight': 0.6942151968028537, 'ratio': 0.10619648424454017, 'aggregation': 'mean', 'treatment': 'removal'}. Best is trial 93 with value: 0.9076936562210944.


 - Metrics: Accuracy=0.9575, F1=0.9015, Recall=0.8492, Precision=0.9607
Done. Results written to wiki-cs_experimentations\wikics_sar_learnable_params_2702031345.csv.
Average F1 over 5 seeds: 0.8959 ± 0.0046
Running experiment with seed=1:
 - alpha=0.5, K=29, layers=1, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.6520900081642776
 - ratio=0.1301604391586133, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 1.8344, LPL: 2.8131, Contrastive: 0.0001
 - Metrics: Accuracy=0.9561, F1=0.9006, Recall=0.8694, Precision=0.9342
Running experiment with seed=2:
 - alpha=0.5, K=29, layers=1, hidden=256, out=256
 - norm=None, dropout=0, margin=0.5, lpl_weight=0.6520900081642776
 - ratio=0.1301604391586133, pos_weight=1, aggregation=mean, treatment=removal
Epoch 0, Loss: 1.8131, LPL: 2.7804, Contrastive: 0.0001
 - Metrics: Accuracy=0.9596, F1=0.9089, Recall=0.8806, Precision=0.9391
Running experiment with seed=3:
 - alpha=0.5, K=29, layers=1, hidden=256, out=256

[I 2025-02-27 03:17:37,071] Trial 99 finished with value: 0.9078176666989897 and parameters: {'K': 29, 'layers': 1, 'hidden_channels': 256, 'out_channels': 256, 'lpl_weight': 0.6520900081642776, 'ratio': 0.1301604391586133, 'aggregation': 'mean', 'treatment': 'removal'}. Best is trial 99 with value: 0.9078176666989897.


 - Metrics: Accuracy=0.9597, F1=0.9092, Recall=0.8802, Precision=0.9402
Done. Results written to wiki-cs_experimentations\wikics_sar_learnable_params_2702031541.csv.
Average F1 over 5 seeds: 0.9078 ± 0.0037
Best trial:
  Average F1: 0.9078176666989897
  Best parameters:
    K: 29
    layers: 1
    hidden_channels: 256
    out_channels: 256
    lpl_weight: 0.6520900081642776
    ratio: 0.1301604391586133
    aggregation: mean
    treatment: removal
